# Global Food Prices

Get dataset

In [92]:
import os
from download import download
import pandas as pd
from matplotlib import pyplot as plt

%matplotlib inline

url_2 = "https://raw.githubusercontent.com/lukes/ISO-3166-Countries-with-Regional-Codes/master/all/all.csv"
regional_file_name = "regions.csv"

url = "http://vam.wfp.org/sites/data/WFPVAM_FoodPrices_05-12-2017.csv"
file_name = 'WFPVAM_FoodPrices_05-12-2017.csv'

def get_dataset(url, file_name):
    if not os.path.isfile(file_name):
        download(url, file_name)
    
    return pd.read_csv(file_name, encoding='latin-1')

df = get_dataset(url, file_name)

region_df = get_dataset(url_2, regional_file_name)

In [93]:
# Pre-process
region_df.rename(columns={'name': 'adm0_name'}, inplace=True)
new_regions = region_df.loc[:, ['adm0_name', 'sub-region']]

df_regions = pd.merge(df, new_regions, on='adm0_name', how='left')

df = df_regions.copy()

df['datetime'] = pd.to_datetime(df.mp_year*10000+df.mp_month*100+1, format='%Y%m%d')


In [94]:
import numpy as np
avg_price = df.groupby(['adm0_name', 'cm_name', 'datetime'])['mp_price']
df_means = avg_price.mean().reset_index()


normalized = df_means.groupby(['adm0_name', 'cm_name'])['mp_price'].apply(lambda x: (x - np.mean(x)) / (np.max(x) - np.min(x)))

In [95]:
df_means['mp_price_norm'] = normalized

# only_apples = df_means.loc[df_means['sub-region'] == 'Central Asia'].loc[df_means['cm_name'] == 'Apples']
# print("MAX", only_apples['mp_price'].max(), "MIN", only_apples['mp_price'].min(), "MEAN", only_apples['mp_price'].mean())

In [96]:
# plt.plot(df_means['datetime'], df_means['mp_price'], '-')

# Make a graph per product. Each line represents a country (or region for later).


from bokeh.io import output_file, show, save
# output_notebook()

from bokeh.models import ColumnDataSource, HoverTool
from bokeh.plotting import figure

In [97]:
from bokeh.palettes import Dark2_5 as palette
import itertools
from bokeh.layouts import column

b = df_means.groupby(['cm_name'])

figures = []

idx = 0
for group, row in b:
    color_idx = 0
    country_group = row.groupby(['adm0_name'])
    p = figure(plot_width=800, plot_height=300, x_axis_type='datetime')
    p.title.text = group
    p.legend.click_policy="hide"
    p.legend.location = "top_left"
    
    for group2, row2 in country_group:
        datetime = []
        prices = []
        for i, data in row2.iterrows():
            datetime.append(data['datetime'])
            prices.append(data['mp_price_norm'])
        p.line(datetime, prices, line_width=4, legend=data['adm0_name'], color=palette[color_idx % 5])
        color_idx += 1
    figures.append(p)
    idx += 1
    if idx > 20:
        break

output_file("groups" + ".html")
show(column(figures))


In [98]:
df

adm0_id             adm0_name  adm1_id   adm1_name  mkt_id  mkt_name  \
0             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
1             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
2             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
3             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
4             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
5             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
6             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
7             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
8             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
9             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
10            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
11            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
12            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
13            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
14            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
15            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
16            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
17            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
18            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
19            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
20            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
21            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
22            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
23            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
24            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
25            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
26            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
27            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
28            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
29            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
...         ...                   ...      ...         ...     ...       ...   
643428      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643429      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643430      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643431      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643432      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643433      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643434      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643435      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643436      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643437      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643438      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643439      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643440      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643441      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643442      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643443      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643444      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643445      238  Syrian Arab Republic     2846     Tartous  1130.0   Tartous   
643446  

In [99]:
df.groupby('cm_name').cm_name.count()



cm_name
Apples                                             485
Apples (red)                                      1236
Avocados                                          2213
Bananas                                           4410
Beans                                             4801
Beans (black)                                      957
Beans (butter)                                     422
Beans (catarino)                                   403
Beans (dry)                                       7716
Beans (fava, dry)                                  211
Beans (green, fresh)                              1248
Beans (kidney white)                               155
Beans (magnum)                                     196
Beans (mung)                                       156
Beans (niebe)                                     9581
Beans (niebe, white)                               215
Beans (red)                                       2183
Beans (red, fresh)                                 130
Be

In [100]:
df.cm_name.unique()

array(['Bread', 'Wheat', 'Rice (low quality)', 'Wage (qualified labour)',
       'Livestock (sheep, one-year-old alive female)', 'Fuel (diesel)',
       'Exchange rate', 'Wage (non-qualified labour, non-agricultural)',
       'Rice', 'Beans (white)', 'Potatoes', 'Eggs', 'Meat (chicken)',
       'Sugar', 'Lentils', 'Pasta', 'Tomatoes', 'Oil', 'Cheese (dry)',
       'Carrots', 'Onions', 'Bananas', 'Tea', 'Fuel (petrol-gasoline)',
       'Fish (canned)', 'Apples', 'Milk (camel)', 'Meat (camel)',
       'Tea (sahm)', 'Wheat flour', 'Milk', 'Oil (vegetable)',
       'Rice (white)', 'Meat (pork)', 'Meat (beef)', 'Cabbage',
       'Apples (red)', 'Cucumbers (greenhouse)', 'Fuel (kerosene)',
       'Fish (fresh)', 'Bread (high grade flour)',
       'Bread (first grade flour)', 'Milk (non-pasteurized)',
       'Rice (coarse)', 'Lentils (masur)', 'Oil (palm)',
       'Rice (imported)', 'Sorghum', 'Maize (white)',
       'Cassava meal (gari)', 'Maize', 'Millet', 'Rice (local)',
       'Rice (impo

In [101]:
avg_price = df.groupby(['adm0_name', 'cm_name'])['mp_price']
df_means = avg_price.mean().reset_index()

df_means

adm0_name                                        cm_name  \
0             Afghanistan                                          Bread   
1             Afghanistan                                  Exchange rate   
2             Afghanistan                                  Fuel (diesel)   
3             Afghanistan   Livestock (sheep, one-year-old alive female)   
4             Afghanistan                             Rice (low quality)   
5             Afghanistan  Wage (non-qualified labour, non-agricultural)   
6             Afghanistan                        Wage (qualified labour)   
7             Afghanistan                                          Wheat   
8                 Algeria                                         Apples   
9                 Algeria                                        Bananas   
10                Algeria                                  Beans (white)   
11                Algeria                                          Bread   
12                Algeria                                        Carrots   
13                Algeria                                   Cheese (dry)   
14                Algeria                                           Eggs   
15                Algeria                                  Fish (canned)   
16                Algeria                                  Fuel (diesel)   
17                Algeria                         Fuel (petrol-gasoline)   
18                Algeria                                        Lentils   
19                Algeria                                   Meat (camel)   
20                Algeria                                 Meat (chicken)   
21                Algeria                                   Milk (camel)   
22                Algeria                                            Oil   
23                Algeria                                         Onions   
24                Algeria                                          Pasta   
25                Algeria                                       Potatoes   
26                Algeria                                           Rice   
27                Algeria                                          Sugar   
28                Algeria                                            Tea   
29                Algeria                                     Tea (sahm)   
..                    ...                                            ...   
815             Swaziland                                           Salt   
816             Swaziland                                  Sugar (brown)   
817             Swaziland                                    Wheat flour   
818  Syrian Arab Republic                                  Beans (white)   
819  Syrian Arab Republic                                 Bread (bakery)   
820  Syrian Arab Republic                                   Bread (shop)   
821  Syrian Arab Republic                                         Bulgur   
822  Syrian Arab Republic                                         Cheese   
823  Syrian Arab Republic                                      Chickpeas   
824  Syrian Arab Republic                                          Dates   
825  Syrian Arab Republic                         Fish (sardine, canned)   
826  Syrian Arab Republic                            Fish (tuna, canned)   
827  Syrian Arab Republic                                  Fuel (diesel)   
828  Syrian Arab Republic                                     Fuel (gas)   
829  Syrian Arab Republic                                        Lentils   
830  Syrian Arab Republic           Livestock (sheep, two-year-old male)   
831  Syrian Arab Republic                            Meat (beef, minced)   
832  Syrian Arab Republic                                            Oil   
833  Syrian Arab Republic                                        Parsley   
834  Syrian Arab Republic                                          Pasta   
835  Syrian Arab Republic                                       

In [105]:
for product in df.cm_name.unique():
    #print(product)
    dates = df.loc[df.cm_name == product,'datetime']
    minimum = min(dates)
    maximum = max(dates)
    #print('Min:') 
    #print(minimum)
    #print('Max:')
    #print(maximum)
    countries = df.loc[df.cm_name == product,'adm0_name'].unique()
    #df.cm_name.unique()
    #print(countries)
    second_min = maximum
    for country in countries:
        min_date_country = min(df.loc[(df.cm_name == product) & (df.adm0_name == country),'datetime'])
        max_date_country = max(df.loc[(df.cm_name == product) & (df.adm0_name == country),'datetime'])
        #print(country)
        #print('Min date in {} for {}:'.format(country, product))
        #print(min_date_country)
        #print('Max date in {} for {}:'.format(country, product))
        #print(max_date_country)
        if min_date_country > minimum and min_date_country < second_min:
            second_min = min_date_country
            second_min_country = country
        
        #missing_values = df.drop((df.cm_name == product) & (df.adm0_name == country) & (df.datetime < second_min))
        #missing_values = df[(df.cm_name != product) & (df.adm0_name != country) & (df.datetime > second_min)]
    missing_values = df[(df['cm_name'] != product) & (df['adm0_name'] != country) & (df['datetime'] > second_min)]
    print(missing_values)
            
            
        


        adm0_id             adm0_name  adm1_id   adm1_name  mkt_id  mkt_name  \
70            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
71            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
72            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
73            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
74            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
75            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
76            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
77            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
78            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
79            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
80            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
81            1           Afghanistan   

        adm0_id             adm0_name  adm1_id   adm1_name  mkt_id  mkt_name  \
0             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
1             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
2             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
3             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
4             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
5             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
6             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
7             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
8             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
9             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
10            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
11            1           Afghanistan   

        adm0_id             adm0_name  adm1_id   adm1_name  mkt_id  mkt_name  \
0             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
1             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
2             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
3             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
4             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
5             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
6             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
7             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
8             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
9             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
10            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
11            1           Afghanistan   

        adm0_id             adm0_name  adm1_id   adm1_name  mkt_id  mkt_name  \
2             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
3             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
4             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
5             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
6             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
7             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
8             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
9             1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
10            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
11            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
12            1           Afghanistan      272  Badakhshan   266.0  Fayzabad   
13            1           Afghanistan   

        adm0_id             adm0_name  adm1_id adm1_name  mkt_id mkt_name  \
4900          4               Algeria      344     Alger  1794.0  Algiers   
4901          4               Algeria      344     Alger  1794.0  Algiers   
4902          4               Algeria      344     Alger  1794.0  Algiers   
4903          4               Algeria      344     Alger  1794.0  Algiers   
4904          4               Algeria      344     Alger  1794.0  Algiers   
4905          4               Algeria      344     Alger  1794.0  Algiers   
4906          4               Algeria      344     Alger  1794.0  Algiers   
4907          4               Algeria      344     Alger  1794.0  Algiers   
4908          4               Algeria      344     Alger  1794.0  Algiers   
4909          4               Algeria      344     Alger  1794.0  Algiers   
4910          4               Algeria      344     Alger  1794.0  Algiers   
4911          4               Algeria      344     Alger  1794.0  Algiers   

...

        adm0_id    adm0_name  adm1_id       adm1_name  mkt_id  mkt_name  \
43            1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
220           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
347           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
388           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
519           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
560           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
637           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
681           1  Afghanistan      275           Balkh   267.0     Mazar   
856           1  Afghanistan      275           Balkh   267.0     Mazar   
981           1  Afghanistan      275           Balkh   267.0     Mazar   
1022          1  Afghanistan      275           Balkh   267.0     Mazar   
1153          1  Afghanistan      275           Balkh   267.0     Mazar   
1194          1  Afghanis

        adm0_id    adm0_name  adm1_id       adm1_name  mkt_id  mkt_name  \
43            1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
220           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
347           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
388           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
519           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
560           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
637           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
681           1  Afghanistan      275           Balkh   267.0     Mazar   
856           1  Afghanistan      275           Balkh   267.0     Mazar   
981           1  Afghanistan      275           Balkh   267.0     Mazar   
1022          1  Afghanistan      275           Balkh   267.0     Mazar   
1153          1  Afghanistan      275           Balkh   267.0     Mazar   
1194          1  Afghanis

        adm0_id    adm0_name  adm1_id       adm1_name  mkt_id  mkt_name  \
43            1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
220           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
347           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
388           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
519           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
560           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
637           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
681           1  Afghanistan      275           Balkh   267.0     Mazar   
856           1  Afghanistan      275           Balkh   267.0     Mazar   
981           1  Afghanistan      275           Balkh   267.0     Mazar   
1022          1  Afghanistan      275           Balkh   267.0     Mazar   
1153          1  Afghanistan      275           Balkh   267.0     Mazar   
1194          1  Afghanis

        adm0_id    adm0_name  adm1_id       adm1_name  mkt_id  mkt_name  \
43            1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
220           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
347           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
388           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
519           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
560           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
637           1  Afghanistan      272      Badakhshan   266.0  Fayzabad   
681           1  Afghanistan      275           Balkh   267.0     Mazar   
856           1  Afghanistan      275           Balkh   267.0     Mazar   
981           1  Afghanistan      275           Balkh   267.0     Mazar   
1022          1  Afghanistan      275           Balkh   267.0     Mazar   
1153          1  Afghanistan      275           Balkh   267.0     Mazar   
1194          1  Afghanis

ValueError: min() arg is an empty sequence